In [45]:
from selenium import webdriver 
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import time 
import pandas as pd

#creating a class to scrape data from Rotten Tomatoes
class RottenTomatoesScraperSelenium:
    def __init__(self,url):
        #reinstalling updated chromedriver just in case 
        import chromedriver_autoinstaller as chromedriver
        chromedriver.install()
        
        self.url = url
        self.driver = webdriver.Chrome()
        self.driver.maximize_window()
        self.driver.get(self.url)
        
        self.cookie_selector = '//*[@id="onetrust-accept-btn-handler"]'
        self.next_button_selector = '//*[@id="main-page-content"]/div/div[5]/button'
        self.main_page_movie_selector = 'js-tile-link'
        self.click_movie_selector = '//*[@id="main-page-content"]/div/div[3]/div/div/a[{}]/tile-dynamic/div'
        self.movie_info_selector = '//*[@id="topSection"]/div[1]/score-board/p'
        self.movie_description_selector = '//*[@id="movieSynopsis"]'
        self.extra_movie_info_selector = '#mainColumn > section.panel.panel-rt.panel-box.movie_info.media > div > div > ul'
        
        try:
            cookie_accept = self.driver.find_element(by = By.XPATH, value = self.cookie_selector)
            cookie_accept.click()
            time.sleep(1)
        except:
            time.sleep(2)
            cookie_accept = self.driver.find_element(by = By.XPATH, value = self.cookie_selector)
            cookie_accept.click()
            time.sleep(1)
            
    def load_pages(self, num_pages = 1):
        self.num_pages = num_pages
        for pages in range(num_pages - 1): 
            next_button = self.driver.find_element(by = By.XPATH, value = self.next_button_selector)
            next_button.click()
            time.sleep(4)
        
        self.movies = self.driver.find_elements(by = By.CLASS_NAME, value = self.main_page_movie_selector)
        self.movie_links = [movie.get_attribute('href') for movie in self.movies]
        
        self.page = BeautifulSoup(self.driver.page_source, "html.parser")

        

        
  

In [29]:
test = movie_object.driver

In [34]:
test.page_source
page = BeautifulSoup(test.page_source, "html.parser")
thumbnail_images = [item for item in page.find_all(attrs={'class':'posterImage'})]
print(len(thumbnail_images))

31


In [46]:
url = 'https://www.rottentomatoes.com/browse/movies_at_home/genres:horror?page='
num_pages = 6

In [47]:
import requests 
from bs4 import BeautifulSoup 

In [56]:
# If number of pages is 5 or less the use the following: 
import pandas as pd

class RottenTomatoesScraper(): 
    def __init__(self,url, num_pages): 
        self.url = url + str(num_pages)
        self.num_pages = num_pages
        self.page = BeautifulSoup(requests.get(self.url).text, "html.parser")
        self.movie_links = []
        self.movies_dataframe = pd.DataFrame()
        for i in self.page.find_all(attrs={'class':'js-tile-link'}):
            try: 
                self.movie_links.append('https://www.rottentomatoes.com' + str(i.attrs['href']))
            except: 
                pass 
    
    # If more than 5 pages is required then use this function to pass the list of full movie links from outside
    def full_movie_links(self, movie_links, page):
        self.movie_links = movie_links 
        self.page = page 
        
        
           
    def scrape_movie_data(self):
        
        for movie_link in self.movie_links:
            print(movie_link)
            extra_movie_dict = {}
            movie = BeautifulSoup(requests.get(movie_link).text, "html.parser")
            print(movie.find_all(attrs={ 'class':'panel-body content_body'}))
            extra_movie_info = movie.find_all(attrs={ 'class':'panel-body content_body'})[0]
            extra_movie_list = extra_movie_info.text.replace('  ', '').replace('\n\n\n', '\n').split('\n')
            extra_movie_list = [item for item in extra_movie_list if item != '']
            extra_movie_dict['description'] = extra_movie_list[0] 
            cleaned_movie_list = []
            
            for i in range(1,len(extra_movie_list)):
                if (':' in extra_movie_list[i]) and ('.' not in extra_movie_list[i]): 
                    pass
                else: 
                    extra_movie_list[i-1] = extra_movie_list[i-1] + ' ' + extra_movie_list[i]
                    cleaned_movie_list.append(extra_movie_list[i-1])

            
            for item in cleaned_movie_list: 
                if (':' in item) and ('.' not in item): 
                    key_value_pair = item.split(':')
                    extra_movie_dict[key_value_pair[0].strip()] = key_value_pair[1].strip()
                elif (':' in item) and ('.' in item):
                    idx = item.index(':')
                    extra_movie_dict[item[:idx]] = item[idx + 1:]
        
            self.movies_dataframe = pd.concat([self.movies_dataframe, pd.DataFrame(extra_movie_dict,index = [0])], axis = 0)
        
            
            

    def scrape_movie_scores(self):
        elements = [item for item in self.page.find_all(attrs={'data-qa':'discovery-media-list-item-caption'})]
        thumbnail_images = [item for item in self.page.find_all(attrs={'class':'posterImage'})]
        movie_title = []
        movie_release_date = []
        critics_score = [] 
        audience_score = []
        critics_sentiment = [] 
        audience_sentiment = [] 
        movie_images = []
        
        for item in elements:
            try:
                scores = item.find_all('score-pairs')[0]
                critics_score.append(scores.attrs['criticsscore'])
                audience_score.append(scores.attrs['audiencescore'])
                critics_sentiment.append(scores.attrs['criticssentiment'])
                audience_sentiment.append(scores.attrs['audiencesentiment'])
                movie_title.append(item.text.split('\r\n        \n\r\n            ')[0].replace('\n\n\n\r\n            ',''))
                movie_release_date.append(item.text.split('\r\n        \n\r\n            ')[1].replace(' \r\n          \n',''))
            except:
                pass
        self.movies_dataframe['movie_title'] = movie_title 
        self.movies_dataframe['movie_release_date'] = movie_release_date
        self.movies_dataframe['critics_score'] = critics_score
        self.movies_dataframe['audience_score'] = audience_score
        self.movies_dataframe['critics_sentiment'] = critics_sentiment
        self.movies_dataframe['audience_sentiment'] = audience_sentiment
        
        for item in thumbnail_images:
            try:
                movie_images.append(item.attrs['src'])
            except:
                pass
        self.movies_dataframe['movie_image'] = movie_images 
        self.movies_dataframe = self.movies_dataframe[list(self.movies_dataframe.columns[-7:]) + list(self.movies_dataframe.columns[:-7])]
        self.movies_dataframe.reset_index(drop = True, inplace = True)

        
    
        

        

In [57]:
scraper_object = RottenTomatoesScraper('https://www.rottentomatoes.com/browse/movies_at_home/genres:horror?page=', num_pages)

if num_pages <= 5: 
    pass
else: 
    movie_object = RottenTomatoesScraperSelenium("https://www.rottentomatoes.com/browse/movies_at_home/genres:horror?page=1")
    movie_object.load_pages(num_pages)
    scraper_object.full_movie_links(movie_object.movie_links, movie_object.page)
        

In [58]:
scraper_object.scrape_movie_data()
#scraper_object.scrape_movie_scores()

https://www.rottentomatoes.com/m/blood_2023
[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                Jess (Michelle Monaghan), a nurse and mother recently separated from her husband (Skeet Ulrich), moves her daughter Tyler (Skylar Morgan Jones) and young son Owen (Finlay Wojtak-Hissong) back into her family farmhouse. Shortly after settling in, Owen's dog escapes into the woods and returns days later, blood-soaked and rabid. When the dog attacks and bites him, the resulting infection grows more shocking as Owen's behavior becomes frightening and deadly. As he spirals deeper into the depths of the illness, Jess discovers a disturbing cure, which makes her question how far she is willing to go to keep her child alive.
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa=

[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                Hannah Blair tells people stories, predicts their future and even dabbles in communicating with the dead. One stormy night that all changes when she meets Rachel, who is actually a dead, lost spirit. Emboldened by this event, she is determined to find out the truth about what happened to her parents' years before. Hannah embarks on a journey into the netherworld where she comes face to face with the Entity. An evil who has haunted mankind since the dawn of time and who now wants Hannah!
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Genre:</div>
<div class="meta-value genre" data-qa="movie-info-item-value">
                   

[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                Helen navigates a ravaged world with her boyfriend Kevin and her little brother Barney. Desperate to find help after Barney's infection slowly turns him into a zombie, they come upon a house where lives Dan, a man harboring a heavy secret.
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Genre:</div>
<div class="meta-value genre" data-qa="movie-info-item-value">
                        
                        Horror, 
                        
                        Mystery &amp; thriller
                        
                    </div>
</li>
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label sub

[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                After witnessing a grotesque murder at a party in her new town, a teenager starts having strange visions and bizarre desires.
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Genre:</div>
<div class="meta-value genre" data-qa="movie-info-item-value">
                        
                        Horror, 
                        
                        Mystery &amp; thriller
                        
                    </div>
</li>
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Original Language:</div>
<div class="meta-value" data-qa="movie-info-item-val

[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                Since childhood, Alex has been a big fan of the fantasy film saga Arthur and the Minimoys. So his best friends surprise him with a special present for his 18th birthday: a trip to the abandoned country house where the saga was set. What begins as a weekend adventure, quickly turns into a deadly nightmare...
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Genre:</div>
<div class="meta-value genre" data-qa="movie-info-item-value">
                        
                        Horror
                        
                    </div>
</li>
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" 

...

[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                Kevin Bacon plays Owen Whistler in this slasher horror film set at an LGBTQIA+ conversion camp. Several queer campers join Whistler for a week of programming intended to "help them find a new sense of freedom". As the camp's methods become increasingly more psychologically unsettling, the campers must work together to protect themselves. When an unidentified axe murderer starts claiming victims, things get even more dangerous.
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Genre:</div>
<div class="meta-value genre" data-qa="movie-info-item-value">
                        
                        Horror, 
                      

[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                A troubled musical prodigy and a new star pupil embark down a sinister path.
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Genre:</div>
<div class="meta-value genre" data-qa="movie-info-item-value">
                        
                        Horror, 
                        
                        Mystery &amp; thriller
                        
                    </div>
</li>
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Original Language:</div>
<div class="meta-value" data-qa="movie-info-item-value">English
                    </div>
</li>
<li 

[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                Six months after the original epidemic, the rage virus has all but annihilated the population of the British Isles. Nevertheless the U.S. Army declares the danger past, and American soldiers arrive to restore order and begin reconstruction. Refugees return to British soil, but one of them carries a deadly secret: The virus is not gone and is even more dangerous than before.
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Rating:</div>
<div class="meta-value" data-qa="movie-info-item-value">R (Some Sexuality/Nudity|Language|Strong Violence and Gore)
                    </div>
</li>
<li class="meta-row clearfix" data-qa="movie-in

[<div class="panel-body content_body">
<div aria-live="polite" class="sr-only js-clamp-live-region"></div>
<div class="movie_synopsis clamp clamp-6 js-clamp" data-qa="movie-info-synopsis" id="movieSynopsis" style="clear:both">
                Adaptation of Bram Stoker's classic vampire novel. Gary Oldman plays Dracula whose lonely soul is determined to reunite with his lost love, Mina (Winona Ryder). In Britain, Dracula begins a reign of terror and seduction draining the life from her closest friend, Lucy (Sadie Frost). Together they try and drive Dracula away.
            </div>
<ul class="content-meta info">
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Rating:</div>
<div class="meta-value" data-qa="movie-info-item-value">R (Sexuality|Horror|Violence)
                    </div>
</li>
<li class="meta-row clearfix" data-qa="movie-info-item">
<div class="meta-label subtle" data-qa="movie-info-item-label">Genre:</d

ValueError: Length of values (175) does not match length of index (180)

In [25]:
scraper_object.movies_dataframe

['https://www.rottentomatoes.com/m/blood_2023',
 'https://www.rottentomatoes.com/m/heretic_2023',
 'https://www.rottentomatoes.com/m/alive_2023',
 'https://www.rottentomatoes.com/m/viking_wolf',
 'https://www.rottentomatoes.com/m/arthur_malediction',
 'https://www.rottentomatoes.com/m/m3gan',
 'https://www.rottentomatoes.com/m/the_menu',
 'https://www.rottentomatoes.com/m/vengeance_2022',
 'https://www.rottentomatoes.com/m/x_2022',
 'https://www.rottentomatoes.com/m/the_offering_2022',
 'https://www.rottentomatoes.com/m/barbarian_2022',
 'https://www.rottentomatoes.com/m/white_noise_2022',
 'https://www.rottentomatoes.com/m/sick_2022',
 'https://www.rottentomatoes.com/m/nope',
 'https://www.rottentomatoes.com/m/theres_something_wrong_with_the_children',
 'https://www.rottentomatoes.com/m/the_innocents_2022',
 'https://www.rottentomatoes.com/m/smile_2022',
 'https://www.rottentomatoes.com/m/hellbender',
 'https://www.rottentomatoes.com/m/pearl_2022',
 'https://www.rottentomatoes.com/m/h

In [60]:
scraper_object.movies_dataframe.to_csv("rotten_tomatoes_horror_movies.csv")